# Histidine Interface Visualization

This notebook visualizes histidine-mediated cation-π and π-π interactions in protein structures.

In [ ]:
# Import required packages
import py3Dmol
import os
import tempfile
from Bio import PDB
from IPython.display import HTML, display
import glob

In [ ]:
# Constants for visualization
CHAIN_A_SURFACE = '#4e79a7'  # Darker blue
CHAIN_A_STICK = '#85b0d5'   # Lighter blue
CHAIN_A_LABEL = '#2c4e6f'   # Dark blue for label text

CHAIN_B_SURFACE = '#f2be2b'  # Gold
CHAIN_B_STICK = '#f2be2b'    # Same as surface
CHAIN_B_LABEL = '#8B4513'    # Dark brown

# Amino acid mapping
ONE_LETTER_MAP = {
    'ALA': 'A', 'ARG': 'R', 'ASN': 'N', 'ASP': 'D',
    'CYS': 'C', 'GLN': 'Q', 'GLU': 'E', 'GLY': 'G',
    'HIS': 'H', 'ILE': 'I', 'LEU': 'L', 'LYS': 'K',
    'MET': 'M', 'PHE': 'F', 'PRO': 'P', 'SER': 'S',
    'THR': 'T', 'TRP': 'W', 'TYR': 'Y', 'VAL': 'V'
}

# Residue type definitions
CATION_RES = {'ARG', 'LYS', 'HIS'}
AROMATIC_RES = {'PHE', 'TYR', 'TRP', 'HIS'}

In [ ]:
def convert_cif_to_pdb(cif_file):
    """Convert a CIF file to PDB format using BioPython."""
    try:
        fd, temp_pdb = tempfile.mkstemp(suffix=".pdb")
        os.close(fd)
        parser = PDB.MMCIFParser(QUIET=True)
        structure = parser.get_structure("structure", cif_file)
        io = PDB.PDBIO()
        io.set_structure(structure)
        io.save(temp_pdb)
        return temp_pdb
    except Exception as e:
        print(f"Error converting {cif_file} to PDB: {e}")
        return None

In [ ]:
def get_sidechain_top_atom(residue):
    """Get the top atom of a residue's sidechain for visualization."""
    if residue.get_resname() == 'HIS':
        return residue['CE1']
    elif residue.get_resname() in {'PHE', 'TYR'}:
        return residue['CZ']
    elif residue.get_resname() == 'TRP':
        return residue['CH2']
    elif residue.get_resname() == 'ARG':
        return residue['CZ']
    elif residue.get_resname() == 'LYS':
        return residue['NZ']
    return None

In [ ]:
def find_histidine_pairs(chain_a, chain_b, distance_cutoff=5.0):
    """Identify cation–π or π–π interactions with at least one HIS residue."""
    pairs = []
    for residue_a in chain_a:
        resn_a = residue_a.get_resname()
        for residue_b in chain_b:
            resn_b = residue_b.get_resname()
            is_a_HIS = (resn_a == 'HIS')
            is_b_HIS = (resn_b == 'HIS')
            is_a_cation_or_aromatic = (resn_a in CATION_RES or resn_a in AROMATIC_RES)
            is_b_cation_or_aromatic = (resn_b in CATION_RES or resn_b in AROMATIC_RES)

            if (is_a_HIS and is_b_cation_or_aromatic) or (is_b_HIS and is_a_cation_or_aromatic):
                for atom_a in residue_a:
                    for atom_b in residue_b:
                        try:
                            if (atom_a - atom_b) < distance_cutoff:
                                if (is_a_HIS and resn_b in CATION_RES) or (is_b_HIS and resn_a in CATION_RES):
                                    itype = '+:π'  # cation–π
                                else:
                                    itype = 'π:π'  # π–π
                                pairs.append((residue_a, residue_b, itype))
                                break
                        except Exception:
                            continue
                    else:
                        continue
                    break
    return pairs

In [ ]:
def create_viewer(pdb_data, viewer_type='ribbon', histidine_pairs=None):
    """Create a py3Dmol viewer with the specified visualization type."""
    viewer = py3Dmol.view(width=800, height=600)
    viewer.addModel(pdb_data, "pdb")
    
    # Add surfaces
    viewer.addSurface(py3Dmol.SAS, {'opacity': 0.6, 'color': CHAIN_A_SURFACE}, {'chain': 'A'})
    viewer.addSurface(py3Dmol.SAS, {'opacity': 0.6, 'color': CHAIN_B_SURFACE}, {'chain': 'B'})
    
    if viewer_type == 'ribbon':
        # Add ribbon view
        viewer.setStyle({'chain': 'A'}, {'cartoon': {'color': CHAIN_A_SURFACE, 'opacity': 1.0}})
        viewer.setStyle({'chain': 'B'}, {'cartoon': {'color': CHAIN_B_SURFACE, 'opacity': 1.0}})
    else:
        # Hide cartoon and show sticks for interacting residues
        viewer.setStyle({'model': -1}, {'cartoon': {'hidden': True}})
        
        if histidine_pairs:
            for resA, resB, itype in histidine_pairs:
                chainA_id = resA.get_parent().id
                chainB_id = resB.get_parent().id
                resA_id = resA.get_id()[1]
                resB_id = resB.get_id()[1]
                
                colorA = CHAIN_A_STICK if chainA_id == 'A' else CHAIN_B_STICK
                colorB = CHAIN_A_STICK if chainB_id == 'A' else CHAIN_B_STICK
                
                viewer.setStyle({'chain': chainA_id, 'resi': resA_id}, 
                               {'stick': {'color': colorA, 'radius': 0.3}})
                viewer.setStyle({'chain': chainB_id, 'resi': resB_id}, 
                               {'stick': {'color': colorB, 'radius': 0.3}})
                
                # Add dotted line between interacting residues
                topA = get_sidechain_top_atom(resA)
                topB = get_sidechain_top_atom(resB)
                if topA and topB:
                    x1, y1, z1 = topA.coord
                    x2, y2, z2 = topB.coord
                    viewer.addLine({
                        'start': {'x': float(x1), 'y': float(y1), 'z': float(z1)},
                        'end': {'x': float(x2), 'y': float(y2), 'z': float(z2)},
                        'color': 'blue',
                        'linewidth': 4,
                        'dashed': True,
                        'dashLength': 0.4,
                        'gapLength': 0.2
                    })
    
    viewer.zoomTo()
    return viewer

In [ ]:
def visualize_structure(file_path):
    """Visualize a structure with both ribbon and labeled views."""
    # Handle CIF files
    if file_path.lower().endswith('.cif'):
        temp_pdb = convert_cif_to_pdb(file_path)
        if not temp_pdb:
            print(f"Could not process CIF file: {file_path}")
            return
        file_path = temp_pdb
    
    # Parse structure
    parser = PDB.PDBParser(QUIET=True)
    structure = parser.get_structure('model', file_path)
    
    try:
        chain_a = structure[0]['A']
        chain_b = structure[0]['B']
    except KeyError:
        print(f"Could not find chain A or B in: {file_path}")
        return
    
    # Find histidine pairs
    histidine_pairs = find_histidine_pairs(chain_a, chain_b, distance_cutoff=5.0)
    
    # Read PDB data
    with open(file_path, 'r') as fh:
        pdb_data = fh.read()
    
    # Create viewers
    ribbon_viewer = create_viewer(pdb_data, 'ribbon')
    label_viewer = create_viewer(pdb_data, 'label', histidine_pairs)
    
    # Display viewers side by side
    display(HTML(f"<div style='display: flex; justify-content: space-between;'>"))
    display(HTML("<div style='width: 48%;'>"))
    ribbon_viewer.show()
    display(HTML("</div>"))
    display(HTML("<div style='width: 48%;'>"))
    label_viewer.show()
    display(HTML("</div>"))
    display(HTML("</div>"))
    
    # Clean up temporary file if it was a CIF
    if file_path.lower().endswith('.cif') and os.path.exists(temp_pdb):
        os.remove(temp_pdb)

In [ ]:
# List available PDB/CIF files
model_files = glob.glob('ndufs-7-acot-9-mm-af2-models/*.pdb') + \
              glob.glob('ndufs-7-acot-9-mm-af2-models/*.cif')
print(f"Found {len(model_files)} model files:")
for i, file in enumerate(model_files):
    print(f"{i+1}. {os.path.basename(file)}")

In [ ]:
# Visualize each model
for i, file_path in enumerate(model_files):
    print(f"\nProcessing model {i+1}: {os.path.basename(file_path)}")
    visualize_structure(file_path)